# Packing CAT Cell demo notebook
The main functions of this demo are located in :
- [chordal_axis_transform.py](../irregular_object_packing/packing/chordal_axis_transform.py)
- [nlc_optimisation.py](../irregular_object_packing/packing/nlc_optimisation.py)


### Contents
1. 
2. 

### Pre-requisites
Please install the required packages using the following command:

```bash
pip install -r requirements.txt
```




In [1]:
# IMPORTS
import numpy as np
import pyvista as pv
import trimesh
from tqdm import tqdm

import sys
sys.path.append('../irregular_object_packing/')
from irregular_object_packing.mesh.transform import scale_and_center_mesh, scale_to_volume, translation_matrix
from irregular_object_packing.mesh.utils import print_mesh_info
from irregular_object_packing.packing.chordal_axis_transform import (
    compute_cat_cells,
    face_coord_to_points_and_faces,
)
from irregular_object_packing.packing.nlc_optimisation import constraints_from_dict, objective, transform_v
from irregular_object_packing.packing.initialize import create_packed_scene, place_objects, save_image
from irregular_object_packing.packing.plots import create_plot

## Basic CAT Cell demo
The cell below shows a simple demo of computing cat faces. The container is a cube and the object os a cuboid rotated 45 degrees over the z axis. The yellow faces are the CAT faces.

In [2]:
from irregular_object_packing.packing.chordal_axis_transform import main
main()

/opt/homebrew/anaconda3/envs/taichi310/lib/python3.10/site-packages/pyvista/core/pointset.py:309: PyVistaDeprecationWarning: You did not specify a value for `inplace` and the default value will be changing to `False` in future versions for point-based meshes (e.g., `PolyData`). Please make sure you are not assuming this to be an inplace operation.
  warnings.warn(DEFAULT_INPLACE_WARNING, PyVistaDeprecationWarning)
/opt/homebrew/anaconda3/envs/taichi310/lib/python3.10/site-packages/pyvista/core/pointset.py:318: PyVistaDeprecationWarning: You did not specify a value for `inplace` and the default value will be changing to `False` in future versions for point-based meshes (e.g., `PolyData`). Please make sure you are not assuming this to be an inplace operation.
  warnings.warn(DEFAULT_INPLACE_WARNING, PyVistaDeprecationWarning)
/opt/homebrew/anaconda3/envs/taichi310/lib/python3.10/site-packages/pyvista/core/pointset.py:327: PyVistaDeprecationWarning: You did not specify a value for `inplac

ViewInteractiveWidget(height=768, layout=Layout(height='auto', width='100%'), width=1024)

## Demo computing CAT cells for Blood Cells in a cylindrical container
The cell below shows a demo of computing cat faces for a cylindrical container and multiple blood cell meshes. The yellow faces are the CAT faces and for each red blood cell there is a corresponding CAT cell. 



In [3]:
mesh_volume = 0.1
container_volume = 10
coverage_rate = 0.3

DATA_FOLDER = "../data/mesh/"
loaded_mesh = trimesh.load_mesh(DATA_FOLDER + "RBC_normal.stl")
print_mesh_info(loaded_mesh, "loaded mesh")
# trimesh.Scene([loaded_mesh]).show()
# Scale the mesh to the desired volume
original_mesh = scale_and_center_mesh(loaded_mesh, mesh_volume)
print_mesh_info(original_mesh, "scaled mesh")

container = trimesh.primitives.Sphere(radius=1, center=[0,0,0])
# container = trimesh.primitives.Cylinder(radius=1, height=1)
print_mesh_info(container, "original container")

container = scale_to_volume(container, container_volume)
print_mesh_info(container, "scaled container")

Mesh info loaded mesh: <trimesh.Trimesh(vertices.shape=(642, 3), faces.shape=(1280, 3))>, 
volume: 71.04896973139347, 
bounding box: [[35.089 37.963 35.089]
 [42.911 40.037 42.911]] 
center of mass: [39. 39. 39.]

Mesh info scaled mesh: <trimesh.Trimesh(vertices.shape=(642, 3), faces.shape=(1280, 3))>, 
volume: 0.10000000000000006, 
bounding box: [[-0.4383 -0.1162 -0.4383]
 [ 0.4383  0.1162  0.4383]] 
center of mass: [-0. -0. -0.]

Mesh info original container: <trimesh.primitives.Sphere>, 
volume: 4.1887902047863905, 
bounding box: [[-1. -1. -1.]
 [ 1.  1.  1.]] 
center of mass: [-0.  0.  0.]

Mesh info scaled container: <trimesh.primitives.Sphere>, 
volume: 9.999999999999996, 
bounding box: [[-1.3365 -1.3365 -1.3365]
 [ 1.3365  1.3365  1.3365]] 
center of mass: [0. 0. 0.]



In [4]:
# Initial placement of the objects
objects_coords = place_objects(container, original_mesh, coverage_rate=coverage_rate, c_scale=0.9)


In [5]:
# get vertices of the object meshes and the container
# we resample to simplify and get a more uniform distribution of points
mesh = trimesh.sample.sample_surface_even(original_mesh, 1000)[0]
obj_points = []
rot_matrices = []
for i in range(len(objects_coords)):
    # get the object
    object = mesh.copy()
    # random rotation
    M_rot = trimesh.transformations.random_rotation_matrix()
    points = trimesh.transform_points(object, M_rot)
    rot_matrices.append(M_rot)
    # apply the transformation
    points = trimesh.transform_points(points, translation_matrix(np.array([0, 0, 0]), objects_coords[i]))

    obj_points.append(points)

container_points = trimesh.sample.sample_surface_even(container, 10000)[0]

In [6]:
# compute the cat cells for each object (takes approx. 1 min)
cat_cells = compute_cat_cells(obj_points, container_points)


2023-02-28 12:14:52.466 (   5.830s) [          5AA766]      vtkDelaunay3D.cxx:519   WARN| vtkDelaunay3D (0x1062dd650): 58 degenerate triangles encountered, mesh quality suspect


In [7]:
def clear_all_key(d):
    """removes the key "all" from the sub-dictionaries of a dictionary"""
    for key in d.keys():
        del d[key]["all"]
    

from scipy.optimize import minimize

# clear_all_key(cat_cells)
# takes to long, just delete for idx 0 now...

del cat_cells[0]["all"]



In [8]:
cat_cells[0]

{(0.2565051933238496,
  0.3732227966743435,
  0.11976822633454358): [[array([0.25059029, 0.41579266, 0.10511868]),
   array([0.24173464, 0.39468571, 0.12314875]),
   array([0.26066286, 0.40290732, 0.14084674])], [array([0.24173464, 0.39468571, 0.12314875]),
   array([0.26066286, 0.40290732, 0.14084674]),
   array([0.23594547, 0.3738775 , 0.1267687 ]),
   array([0.25487369, 0.38209911, 0.1444667 ])], [array([0.26049631, 0.36190937, 0.11323561]),
   array([0.24156809, 0.35368776, 0.09553761]),
   array([0.25042374, 0.37479471, 0.07750755])], [array([0.24701762, 0.35195808, 0.13463224]),
   array([0.25337147, 0.36327936, 0.12963469]),
   array([0.24851985, 0.37077783, 0.14946424]),
   array([0.25487369, 0.38209911, 0.1444667 ])], [array([0.25337147, 0.36327936, 0.12963469]),
   array([0.26049631, 0.36190937, 0.11323561]),
   array([0.26230954, 0.37795472, 0.11965009])], [array([0.26428204, 0.36041772, 0.15247507]),
   array([0.25337147, 0.36327936, 0.12963469]),
   array([0.27322011, 0.37

In [9]:
from irregular_object_packing.packing.nlc_optimisation import constraints_from_dict, objective, transform_v
# for object 0:
    # Define the bounds for the variables
r_bound = (-1 / 12 * np.pi, 1 / 12 * np.pi)
t_bound = (0, 1)
bounds = [(0.1, None), r_bound, r_bound, r_bound, t_bound, t_bound, t_bound]
x0 = np.array([0.9, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01])

init_res = constraints_from_dict(x0, cat_cells[0])

# constraint_dict = {"type": "ineq", "fun": constraints_from_dict, "args": cat_cells[0]}
# res = minimize(objective, x0, method="SLSQP", bounds=bounds, constraints=constraint_dict)



ValueError: setting an array element with a sequence. The requested array has an inhomogeneous shape after 1 dimensions. The detected shape was (1000,) + inhomogeneous part.

In [ ]:

# new_points = [transform_v(point) for point in obj_points[0]]

In [ ]:
# This next part of code is for the visualization of the CAT cells.
# it processes the output of compute_cat_cells to create a PyVista mesh for each object
# and it applies the corresponding transformations on the object meshes.
from irregular_object_packing.packing.nlc_optimisation import construct_transform_matrix

# Volumetric downscale before optimizing the packing
down_scale = 0.1

object_meshes = []
cat_meshes = []
lim = len(cat_cells.keys()) 
k = 0
v = cat_cells[0]
# for k, v in tqdm(cat_cells.items()):
    # if k >= lim - 1:
    #     break
cat_points, poly_faces = face_coord_to_points_and_faces(v["all"])
polydata = pv.PolyData(cat_points, poly_faces)

object_mesh = original_mesh.copy()
object_mesh.apply_transform(rot_matrices[k])
object_mesh.apply_scale(down_scale ** (1 / 3))

post_mesh = object_mesh.copy()

post_mesh.vertices = trimesh.transformations.transform_points(
    post_mesh.vertices, construct_transform_matrix(res.x)
)



In [ ]:
# create_plot(objects_coords, object_meshes, cat_meshes, container.to_mesh())
import pyvista as pv

# create the first plot
plot1 = pv.Plotter()  # replace with the filename/path of your first mesh
plot1.add_mesh(object_mesh, color="red", opacity=0.8)
plot1.add_mesh(polydata, color="yellow", opacity=0.4)

# create the second plot
plot2 = pv.Plotter()
mesh2 = pv.read("mesh2.stl")  # replace with the filename/path of your second mesh
plot2.add_mesh(post_mesh, color="red", opacity=0.8)
plot2.add_mesh(polydata, color="yellow", opacity=0.4)

# set up the rendering window with two horizontal subplots
plotter = pv.Plotter(window_size=[800, 400])
plotter.subplot(1, 2, 0)
plotter.add_subplot(plot1, render=False)
plotter.subplot(1, 2, 1)
plotter.add_subplot(plot2, render=False)

# show the plot
plotter.show()
